In [ ]:
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        #print(os.path.join(dirname, filename))
        pass

# Bu projede  Yaprakların Sağlıklı olup olmadığına göre 4 çeşit guruptan hangilerine girdiklerini kontrol ediceğiz modellimiz için de CNN kullanıcağız 

In [ ]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import warnings
warnings.filterwarnings('ignore') 

import cv2
import os
import tensorflow as tf
from tensorflow.keras.preprocessing.image import ImageDataGenerator
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Conv2D, MaxPooling2D, Flatten, Dense, Dropout
from tensorflow.keras.optimizers import Adam
from sklearn.model_selection import train_test_split

path='/kaggle/input/augmented-grape-disease-detection-dataset/Final Training Data/'

In [ ]:
def create_dataset(folders, path, max_images_per_label=1000):
    data = {'imgpath': [], 'labels': []}
    
    for folder in folders:
        folderpath = os.path.join(path, folder)
        files = os.listdir(folderpath)
        
        # Her bir klasörden sadece max_images_per_label kadar görsel alıyoruz
        selected_files = files[:max_images_per_label]
        
        for file in selected_files:
            filepath = os.path.join(folderpath, file)
            data['imgpath'].append(filepath)
            data['labels'].append(folder)

    dataset = pd.DataFrame(data)
    return dataset

In [ ]:
import os 

sınıf=os.listdir(path)  # Kolon adlarımız 
num_classes = len(os.listdir(path))
print('Sınıflarımız: ',sınıf,'\nSınıf sayisi:',num_classes)

In [ ]:
folders1 = ['ESCA', 'Healthy', 'Leaf Blight', 'Black Rot']
df=create_dataset(folders1,path)
df.head()

In [ ]:
df.info()

In [ ]:
import cv2
import matplotlib.pyplot as plt
for index, row in df.sample(7).iterrows():
    # Resmi yükle
    img = cv2.imread(row['imgpath'])
    
    # OpenCV resmi RGB formatına dönüştür
    img_rgb = cv2.cvtColor(img, cv2.COLOR_BGR2RGB)
    
    # Resmi matplotlib ile göster
    plt.figure(figsize=(6, 6))
    plt.imshow(img_rgb)
    plt.title(row['labels'])
    plt.axis('off')
    plt.show()

In [ ]:
import warnings
warnings.filterwarnings('ignore')
import matplotlib.pyplot as plt
import plotly.express as px

sayi = df['labels'].value_counts() #hurma türe göre sayisi 
 
# Plotly ile hurma dağılımını görselleştirme
fig=px.bar(x=sayi.index,  #6 indexi var
           y=sayi.values, # sayisi 
           color=sayi.index, # rekleri yine sayisina göre
           labels={'x': 'Çeşitler','y': 'Toplam Sayı'}, #label yazdırma
           title='Yaprak Çeşitleri Grafiği', #başlık 
           template='plotly_dark') # arkapılan 

fig.show()


fig = px.pie(names=sayi.index,
             values=sayi.values,
             title='Yaprak Dağılımı',
             labels={'names': 'Hurma',
                     'values': 'Toplam Sayı'},
             template='plotly_white')
fig.show()

![yaprak](https://www.mdpi.com/agriculture/agriculture-11-00707/article_deploy/html/images/agriculture-11-00707-g004.png)

# Normalizasyon

In [ ]:
df = df.sample(frac=1).reset_index(drop=True)

In [ ]:
import numpy as np
x=[]
for img in df['imgpath']:
    try:
        img = cv2.imread(img)
        img = cv2.resize(img, (128, 128))# 128 pixle boyutunda
        img = img / 255.0  # normalize etmee 
        x.append(img)      # img 

    except:
        print(f"Error loading image: {img}")

# Modelin

In [ ]:
from sklearn.preprocessing import LabelEncoder
encoder = LabelEncoder()

# Etiketleri sayısal değerlere dönüştür
df['encode_label'] = encoder.fit_transform(df['labels'])

In [ ]:
x=np.array(x)
y=df['encode_label']

from sklearn.model_selection import train_test_split
x_train, x_test, y_train, y_test = train_test_split(x, y, test_size=0.25, random_state=42)

x_train.shape,x_test.shape

In [ ]:
import tensorflow as tf
from tensorflow.keras import layers, models

In [ ]:
model = models.Sequential()

# Evrişimsel katmanlar(Conv) ve havuzlama(pooling) katmanları

model.add(layers.Conv2D(32, (3, 3), activation='relu', input_shape=(128, 128, 3)))
model.add(layers.MaxPooling2D((2, 2)))
model.add(layers.Dropout(0.25))   # overfiting yapasın diye bazı değerleri atıyoruz dropout ile

model.add(layers.Conv2D(64, (3, 3), activation='relu'))
model.add(layers.MaxPooling2D((2, 2)))
model.add(layers.Dropout(0.25))

model.add(layers.Conv2D(128, (3, 3), activation='relu'))
model.add(layers.MaxPooling2D((2, 2)))
model.add(layers.Dropout(0.25))

model.add(layers.Conv2D(128, (3, 3), activation='relu'))
model.add(layers.MaxPooling2D((2, 2)))
model.add(layers.Dropout(0.25))

model.add(layers.Conv2D(256, (3, 3), activation='relu'))
model.add(layers.MaxPooling2D((2, 2)))
model.add(layers.Dropout(0.25))

# Düzleştirme ve tam bağlı katmanlar
model.add(layers.Flatten())  # düzleştirme

model.add(layers.Dense(512, activation='relu'))
model.add(layers.Dropout(0.5))  # Yüksek dropout oranı, tam bağlı katmanlarda aşırı öğrenmeyi azaltabilir
model.add(layers.Dense(4, activation='softmax'))  # Çıkış katmanı: 4 sınıf için # çeşit sayımıza göre 

# Modeli derleme
model.compile(optimizer='adam',loss='sparse_categorical_crossentropy',metrics=['accuracy'])



In [ ]:
model.summary()

In [ ]:
import warnings
warnings.filterwarnings('ignore')

history = model.fit(x_train, y_train, validation_data=(x_test, y_test), epochs=30, batch_size=150)


In [ ]:
# Sonçlar çok iyi 
model.save('model_leaf_99.h5')

In [ ]:
# Eğitim ve Doğrulama Kaybı
plt.plot(history.history['loss'], label='Eğitim Kaybı')
plt.plot(history.history['val_loss'], label='Doğrulama Kaybı')
plt.xlabel('Epoch')
plt.ylabel('Loss')
plt.legend()
plt.show()

# Eğitim ve Doğrulama Doğruluğu
plt.plot(history.history['accuracy'], label='Eğitim Doğruluğu')
plt.plot(history.history['val_accuracy'], label='Doğrulama Doğruluğu')
plt.xlabel('Epoch')
plt.ylabel('Accuracy')
plt.legend()
plt.show()

In [ ]:
loss,acc=model.evaluate(x_test,y_test)

In [ ]:
acc

In [ ]:
predict=model.predict(x_test)
import seaborn as sns
import matplotlib.pyplot as plt
from sklearn.metrics import confusion_matrix
import numpy as np


sns.heatmap(confusion_matrix(y_test, np.argmax(predict, axis=1)), annot=True, fmt='d', annot_kws={"size": 16})
plt.title('Confusion Matrix', fontsize=18)
plt.show()


# Burada 1000 tane gözükemsinin nedeni bizim test değerlerimizin adedi oluyor 4000 göresl üzernde işlem yaptık 1000 tansei test ,3000 train

In [ ]:
print(classification_report(y_test,np.argmax(predict,axis=1)))


## Sonuç olarak CNN ile İyi bir model Skoruna gelebildik  , biz bu modeli applerimizde kullanmak için save edeceğiz

In [ ]:
model.save('model_leaf.h6')